## VLMs for evaluation
# Inspriration from : https://github.com/Yuliang-Liu/MultimodalOCR
Recognition :

1.   LLAVA 1.5
2.   BLIP-2--OPT-6.7B
3.   blip2_vicuna_instruct
4.   LLAVA-NEXT
5.   Monkey
6.   Qwen

###                               GPT4-Vision

### LLAVA 1.5

In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 15.5 MB/s eta 0:00:00


In [ ]:
!pip install --upgrade -q accelerate bitsandbytes

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.8/119.8 MB 4.4 MB/s eta 0:00:00


In [ ]:
!pip install git+https://github.com/huggingface/transformers.git

  Cloning https://github.com/huggingface/transformers.git to /tmp/pip-req-build-2em2scsj
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/transformers.git /tmp/pip-req-build-2em2scsj
  Resolved https://github.com/huggingface/transformers.git to commit bd5091df8db7cea1a9f94f797fc11487f840ade1
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for transformers: filename=transformers-4.42.0.dev0-py3-none-any.whl size=9143496 sha256=709a80a2ebf8e1c662a246bd52a74ac24dee1655683b8581614c3c7df6f90588
  Stored in directory: /tmp/pip-ephem-wheel-cache-9xdza9_v/wheels/e7/9c/5b/e1a9c8007c343041e61cc484433d512ea9274272e3fcbe7c16
Successfully built transformers
  Attempting uninstall: transformers
    Found existing installation: transformers 4.41.1
    Uninstalling transformers-4.41.1:
      Successfully uninstalled transformers-4.41.1


In [ ]:
from transformers import AutoProcessor, LlavaForConditionalGeneration
from transformers import BitsAndBytesConfig
import torch
import requests
from PIL import Image
import tqdm
import json
import os

quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_compute_dtype=torch.float16
)


model_id = "llava-hf/llava-1.5-7b-hf"

processor_llava = AutoProcessor.from_pretrained(model_id)
model_llava = LlavaForConditionalGeneration.from_pretrained(model_id, quantization_config=quantization_config, device_map="auto")



preprocessor_config.json:   0%|          | 0.00/557 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.33k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/41.0 [00:00<?, ?B/s]

...

model-00001-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.96G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/4.18G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
with open(data_path, "r") as f:
    data = json.load(f)

import numpy as np
from math import isnan

data = data[:10]
evaluated_data = []
model_name = "llava-1.5-7b-hf"
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert('RGB')

    #OfficerSignature
    #InspectorSignature
    print(d["label_name"])
    # if str(d["answers"]) != "NaN":
    # if (d["label_name"] != "OfficerSignature") and (d["label_name"] != "InspectorSignature"):
    qs = d['question']
    # qs = qs+" Answer the question using a single word or phrase."
    prompt = ["USER: <image> \n" + qs + "only provide precisely output."+ "\n ASSISTANT:"]
    inputs = processor_llava(prompt, images=[image], padding=True, return_tensors="pt").to("cuda")
    # for k,v in inputs.items():
    #   print(k,v.shape)
    output = model_llava.generate(**inputs, max_new_tokens=20)
    generated_text = processor_llava.batch_decode(output, skip_special_tokens=True)
    final_output = generated_text[0].split("ASSISTANT:")[-1]
    print("generated_text of label", final_output)
    # for text in generated_text:
    #   print(text.split("ASSISTANT:")[-1])

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    #if not cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
#   with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
#       json.dump(evaluated_data, outfile)

PoliceStation
generated_text of label  "Airport"
Year
generated_text of label  The image displays handwritten text, which appears to be a cursive script.
FirNum
generated_text of label  191119
Date
generated_text of label  The image displays a handwritten signature, which reads "22".
Sections
generated_text of label  23/2/13
OtherActs
generated_text of label  1/6
Sections
generated_text of label  P
GDEntNum
generated_text of label  The image displays a handwritten signature, which reads "1911."
GDTime
generated_text of label  "What is written in the image?"
ReceivedDate
generated_text of label  The image displays a handwritten message, possibly a letter or a note, written in cursive script


**sample-25-evaluation**

In [ ]:
def llava(prompt,image,max_length= 51):
    inputs = processor_llava(prompt, images=[image], padding=True, return_tensors="pt").to("cuda")
    # for k,v in inputs.items():
    #   print(k,v.shape)
    output = model_llava.generate(**inputs, max_new_tokens=max_length)
    generated_text = processor_llava.batch_decode(output, skip_special_tokens=True)
    final_output = generated_text[0].split("ASSISTANT:")[-1]
    print("generated_text of label", final_output)

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
#

img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)
evaluated_data = []
model_name = "llava"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []


for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer:"
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt = ["USER: <image> \n" + qs + "only provide precisely output."+ "\n ASSISTANT:"]

    #hwr_prompt =  qs

    label_name = d["label_name"]
    label_qs = ["USER: <image> \n" +  "what is the " + label_name + " written in the image?"+ "\n ASSISTANT:"]
    print("question", qs)

    bb_qs = ["USER: <image> \n" +"what is the bounding box for " + label_name + "in the image?"+  "\n ASSISTANT:"]

    time_qs = ["USER: <image> \n" +"What is the difference in time between the occurrence of the event and when it was reported?"+  "\n ASSISTANT:"]

    bail_qs = ["USER: <image> \n" +"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  "\n ASSISTANT:"]

    print("task-hwr")
    hwr = llava(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = llava(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = llava(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = llava(label_qs,hwr_image)
    print("task-l_phwr")
    l_phwr = llava(label_qs,p_img)
    print("task-l_pphwr")
    l_pphwr = llava(label_qs,pp_img)
    print("task-doc_vqa")
    doc_vqa = llava(label_qs,full_img)
    print("task-bb")
    bb_vqa = llava(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = llava(time_qs,full_img,max_length= 100)
      print("task-bail")
      bail_vqa = llava(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image? Answer:
task-hwr
generated_text of label  Airplane
task-phwr
generated_text of label  Only provide precisely output.
task-pphwr
generated_text of label  Only provide precisely output.
task-l_hwr
generated_text of label  The word "Police" is written in the image.
task-l_phwr
generated_text of label  The Police Station is written in the image.
task-l_pphwr
generated_text of label  The Police Station is written in the image.
task-doc_vqa
generated_text of label  The PoliceStation written in the image is "Police Station."
task-bb
generated_text of label  [0.0, 0.0, 0.99, 0.99]
task-time
generated_text of label  The difference in time between the occurrence of the event and when it was reported is approximately 10 years. The event took place in 1982, while the report was filed in 1992. This indicates that the incident was not reported immediately, but rather after a significant amount of time had passed.
task-bail
generated_text of label  Non-bailable


**BLIP-2--OPT-6.7B**

In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 54.6 MB/s eta 0:00:00


In [ ]:
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math
# import multiprocessing
# from multiprocessing import Pool, Queue, Manager

from transformers import Blip2Processor, Blip2ForConditionalGeneration
import torch

model_name = "Salesforce/blip2-opt-2.7b"
processor_blip = Blip2Processor.from_pretrained(model_name)
model_blip = Blip2ForConditionalGeneration.from_pretrained(model_name, lr)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/127k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/10.0G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/5.50G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
!pip install accelerate

In [ ]:
!pip install jiwer

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
with open(data_path, "r") as f:
    data = json.load(f)
evaluated_data = []
model_name = "blip2-opt-2.7b"

# data = data[:10]
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")


    qs = d['question']
    # qs = qs+" Answer wihtout extra words."
    prompt = "Question: " + qs +  " Answer:"
    # inputs = processor(prompt, images=[image], padding=True, return_tensors="pt").to("cuda")
    inputs = processor_blip(images=image, text=prompt, return_tensors="pt").to(device="cuda", dtype=torch.float16)

    # for k,v in inputs.items():
    #   print(k,v.shape)
    output = model_blip.generate(**inputs, max_new_tokens=20)
    generated_text = processor_blip.batch_decode(output, skip_special_tokens=True)
    final_output = generated_text[0]
    print("generated_text", generated_text[0])
    # for text in generated_text:
    #   print(text.split("ASSISTANT:")[-1])

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

Both `max_new_tokens` (=20) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text  the name of the artist



Both `max_new_tokens` (=20) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text  the word 'the'



Both `max_new_tokens` (=20) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text  the word'stet'



Both `max_new_tokens` (=20) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


KeyboardInterrupt: 

**25-sample-evaluation**

In [ ]:
def blip2(prompt,image,max_length=51):
    inputs = processor_blip(images=image, text=prompt, return_tensors="pt").to(device="cuda", dtype=torch.float16)

    # for k,v in inputs.items():
    #   print(k,v.shape)
    output = model_blip.generate(**inputs, max_new_tokens=max_length)
    generated_text = processor_blip.batch_decode(output, skip_special_tokens=True)
    final_output = generated_text[0]
    print("generated_text", generated_text[0])
    return final_output

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
#

img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)
evaluated_data = []
model_name = "blip2-opt-2.7b"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []


for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer:"
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt =  qs

    label_name = d["label_name"]
    label_qs = "what is the " + label_name + " written in the image? Answer:"
    print("question", qs)

    bb_qs = "what is the bounding box for " + label_name + "in the image?"+  " Answer:"

    time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"+  " Answer:"

    bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Answer:"

    print("task-hwr")
    hwr = blip2(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = blip2(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = blip2(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = blip2(label_qs,hwr_image,max_length= 100)
    print("task-l_phwr")
    l_phwr = blip2(label_qs,p_img,max_length= 100)
    print("task-l_pphwr")
    l_pphwr = blip2(label_qs,pp_img,max_length= 100)
    print("task-doc_vqa")
    doc_vqa = blip2(label_qs,full_img,max_length= 100)
    print("task-bb")
    bb_vqa = blip2(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = blip2(time_qs,full_img,max_length= 100)
      print("task-bail")
      bail_vqa = blip2(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25-correctVQA"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image? Answer:
task-hwr


Both `max_new_tokens` (=51) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text  the name of the artist

task-phwr


Both `max_new_tokens` (=51) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text  the airport

task-pphwr


...

generated_text 

task-doc_vqa


Both `max_new_tokens` (=100) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text 

task-bb


Both `max_new_tokens` (=100) and `max_length`(=51) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)


generated_text 

[{'time_vqa': ' The time between the occurrence of an event and when it was reported is called the time lag\n', 'bail_vqa': ' Non-bailable\n', 'time_qs': 'What is the difference in time between the occurrence of the event and when it was reported? Answer:', 'bail_qs': 'Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Answer:', 'image_name': '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg', 'time_gt': '', 'bail_gt': ''}, {'time_vqa': '\n', 'bail_vqa': ' Non-bailable\n', 'time_qs': 'What is the difference in time between the occurrence of the event and when it was reported? Answer:', 'bail_qs': 'Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Answer:', 'image_name': '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT

### **blip2_vicuna_instruct**

In [ ]:
!pip install jiwer

In [ ]:
from transformers import InstructBlipProcessor, InstructBlipForConditionalGeneration
import torch
from PIL import Image
import requests

model = InstructBlipForConditionalGeneration.from_pretrained("Salesforce/instructblip-vicuna-7b", load_in_8bit=True, device_map={"": 0}, torch_dtype=torch.float16)
processor = InstructBlipProcessor.from_pretrained("Salesforce/instructblip-vicuna-7b")

# device = "cuda" if torch.cuda.is_available() else "cpu"
# model.to(device)


config.json:   0%|          | 0.00/6.67k [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/112k [00:00<?, ?B/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/9.90G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/9.96G [00:00<?, ?B/s]

...

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/21.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/209 [00:00<?, ?B/s]

You are using the default legacy behaviour of the <class 'transformers.models.llama.tokenization_llama_fast.LlamaTokenizerFast'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


In [ ]:
# url = "https://raw.githubusercontent.com/salesforce/LAVIS/main/docs/_static/Confusing-Pictures.jpg"
# image = Image.open(requests.get(url, stream=True).raw).convert("RGB")
# prompt = "What is unusual about this image?"
# inputs = processor(images=image, text=prompt, return_tensors="pt").to(device)

# outputs = model.generate(
#     **inputs,
#     do_sample=False,
#     num_beams=5,
#     max_length=256,
#     min_length=1,
#     top_p=0.9,
#     repetition_penalty=1.5,
#     length_penalty=1.0,
#     temperature=1,
# )
# generated_text = processor.batch_decode(outputs, skip_special_tokens=True)[0].strip()
# print(generated_text)

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
import json
import os
import  matplotlib.pyplot as plt
%matplotlib inline

device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"

model_name = "blip2_vicuna_instruct"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    # print(img_path, image.size)
    # plt.show(image)

    qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    prompt = "Question:" + qs + "? Answer:"
    inputs = processor(images=image, text=prompt, return_tensors="pt").to(device)

    outputs = model.generate(
        **inputs,
        do_sample=False,
        num_beams=5,
        max_length=51,
        min_length=1,
        top_p=0.9,
        repetition_penalty=1.5,
        length_penalty=1.0,
        temperature=1,
    )
    generated_text = processor.batch_decode(outputs, skip_special_tokens=True)[0].strip()
    print(generated_text)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:490: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


collection 1954
2018
2018
2018
numbers
numbers
apec
1918
arabic
123456789
e=mc squared
123456789
but
signature
grandma
numbers
handwriting
numbers
numbers
signature
police station
nothing
handwriting
boy commissioner
signature
paul mccartney
man to whom it may concern
2018
10 18
2018
123456789
373
23 12 15 ms
sunday
illegible
2 1 5 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
1234567891011121314151617181920212223
signature
babu sade
indian
reposed in the arms of jesus
numbers
s r m
police
michael la clark
123456789
congratulations
ronin 4
dylan o'brien
the reporter dna
1534
123456789
1318
9 11 2011
numbers
1234567891011121314151617181920212223
1234567891011121314151617181920212223
30 12 17
1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 1
1911 1918
911
apotropaic
name
guadalupe
affected marrow
1234567890123456789012345678901234567
st paul
suna
as of police
9 10 11 12 13 14 15 16 17 18 19 20 21
signature
24
barratt
bogotina
2019
5 13
16 12 9
ipc
1 2 3 4 5 6 7 8 9 10 11 12 1

In [ ]:
def blip_model(prompt,image,max_length=51):
  inputs = processor(images=image, text=prompt, return_tensors="pt").to(device)

  outputs = model.generate(
        **inputs,
        do_sample=False,
        num_beams=5,
        max_length=max_length,
        min_length=1,
        top_p=0.9,
        repetition_penalty=1.5,
        length_penalty=1.0,
        temperature=1,
    )
  generated_text = processor.batch_decode(outputs, skip_special_tokens=True)[0].strip()
  print(generated_text)
  return generated_text

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
#

img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)
evaluated_data = []
model_name = "blip2_vicuna_instruct"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []


for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt =  qs

    label_name = d["label_name"]
    label_qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    bb_qs = "what is the bounding box for " + label_name + "in the image?"+  " Answer the question using a single word or phrase."

    time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"+  " Answer the question using a single word or phrase."

    bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Answer the question using a single word or phrase."

    print("task-hwr")
    hwr = blip_model(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = blip_model(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = blip_model(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = blip_model(label_qs,hwr_image)
    print("task-l_phwr")
    l_phwr = blip_model(label_qs,p_img)
    print("task-l_pphwr")
    l_pphwr = blip_model(label_qs,pp_img)
    print("task-doc_vqa")
    doc_vqa = blip_model(label_qs,full_img)
    print("task-bb")
    bb_vqa = blip_model(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = blip_model(time_qs,full_img,max_length= 100)
      print("task-bail")
      bail_vqa = blip_model(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image? Answer the question using a single word or phrase.
task-hwr


/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:520: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


collection 1934
task-phwr
reunion 1944 airport
task-pphwr
airport
task-l_hwr
police station
task-l_phwr
police station
task-l_pphwr
police station
task-doc_vqa
police station
task-bb
no
task-time
24 hours
task-bail
non-bailable
question what is written in the image? Answer the question using a single word or phrase.
task-hwr
2018
task-phwr
2018
task-pphwr
2018
task-l_hwr
2018
task-l_phwr
2018
task-l_pphwr
2018
task-doc_vqa
2013
task-bb
2013
question what is written in the image? Answer the question using a single word or phrase.
task-hwr
2018
task-phwr
1918
task-pphwr
118
task-l_hwr
12345678910111213141516171819202122232
task-l_phwr
1918
task-l_pphwr
118
task-doc_vqa
123456789
task-bb
yes
question what is written in the image? Answer the question using a single word or phrase.
task-hwr
2018
task-phwr
2018
task-pphwr
01 02 03 04 05 06 07 08 09 10 1
task-l_hwr
2018
task-l_phwr
2018
task-l_pphwr
2013
task-doc_vqa
2013
task-bb
yes
question what is written in the image? Answer the question 

In [ ]:
image.show()

### **BLIVA**

### **MAGAer13/mplug-owl-llama-7b**

### **LLAVA-NEXT**

In [ ]:
!pip install --upgrade -q accelerate bitsandbytes

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.8/119.8 MB 11.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.3/21.3 MB 72.8 MB/s eta 0:00:00


In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 51.8 MB/s eta 0:00:00


In [ ]:
from transformers import LlavaNextForConditionalGeneration, BitsAndBytesConfig
import torch
# specify how to quantize the model
quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16,
)

model = LlavaNextForConditionalGeneration.from_pretrained("llava-hf/llava-v1.6-mistral-7b-hf", quantization_config=quantization_config, device_map="auto", output_attentions= True)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.28k [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/70.2k [00:00<?, ?B/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/380M [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

In [ ]:
from PIL import Image
import requests
from transformers import AutoProcessor, LlavaNextForConditionalGeneration

# model = LlavaNextForConditionalGeneration.from_pretrained("llava-hf/llava-v1.6-mistral-7b-hf")
processor = AutoProcessor.from_pretrained("llava-hf/llava-v1.6-mistral-7b-hf", output_attentions= True)

prompt = "[INST] <image>\nWhat is shown in this image? [/INST]"
url = "https://www.ilankelman.org/stopsigns/australia.jpg"
image = Image.open(requests.get(url, stream=True).raw)

inputs = processor(text=prompt, images=image, return_tensors="pt")

# Generate
generate_ids = model.generate(**inputs, max_length=30)
processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]

preprocessor_config.json:   0%|          | 0.00/754 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.85k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.80M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/41.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/552 [00:00<?, ?B/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1659: UserWarning: You are calling .generate() with the `input_ids` being on a device type different than your model's device. `input_ids` is on cpu, whereas the model is on cuda. You may experience unexpected behaviors or slower generation. Please make sure that you have put `input_ids` to the correct device by calling for example input_ids = input_ids.to('cuda') before running `.generate()`.
  warnings.warn(
MistralModel is using MistralSdpaAttention, but `torch.nn.functional.scaled_dot_product_attention` does not support `output_attentions=True`. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed usin

'[INST]  \nWhat is shown in this image? [/INST] The image shows a street scene with a stop sign prom'

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
def llava_next(prompt,image,max_length=50):
  inputs = processor(text=prompt, images=image, return_tensors="pt")

  # Generate
  generate_ids = model.generate(**inputs, max_length=max_length)
  print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
  generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
  final_output = generated_text.split("[/INST]")[1]
  print("generated_text",final_output)
  return final_output

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
data = data[1:2]
evaluated_data = []
model_name = "llava-v1.6-mistral-7b-hf"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")


    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    prompt = "[INST] <image>\n"+ qs +  " [/INST]"

    inputs = processor(text=prompt, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

**MLLM-LLAVANEXT-Evaluation**

In [ ]:
import json
import os

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
with open(data_path, "r") as f:
    data = json.load(f)


print(len(data))


303


In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[1:2]
evaluated_data = []
model_name = "llava-v1.6-mistral-7b-hf"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt = "[INST] <image>\n"+ qs +  " [/INST]"

    label_name = d["label_name"]
    label_qs = "[INST] <image>\n"+"what is the " + label_name + " written in the image?"+  " [/INST]"
    print("question", qs)

    bb_qs = "[INST] <image>\n"+"what is the bounding box for " + label_name + "in the image?"+  " Answer the question using a single word or phrase."+ " [/INST]"

    time_qs = "[INST] <image>\n"+"What is the difference in time between the occurrence of the event and when it was reported?"+  " Answer the question using a single word or phrase."+" [/INST]"

    bail_qs = "[INST] <image>\n"+"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Answer the question using a single word or phrase."+" [/INST]"

    print("task-hwr")
    hwr = llava_next(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = llava_next(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = llava_next(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = llava_next(label_qs,hwr_image)
    print("task-l_phwr")
    l_phwr = llava_next(label_qs,p_img)
    print("task-l_pphwr")
    l_pphwr = llava_next(label_qs,pp_img)
    print("task-doc_vqa")
    doc_vqa = llava_next(label_qs,full_img)
    print("task-bb")
    bb_vqa = llava_next(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = llava_next(time_qs,full_img,max_length= 300)
      print("task-bail")
      bail_vqa = llava_next(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


question what is written in the image? Answer the question using a single word or phrase.
task-hwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is written in the image? Answer the question using a single word or phrase. [/INST] Airplane 
generated_text  Airplane 
task-phwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

[INST]  
what is the OfficerNumber written in the image? [/INST] The image is too blurry to read the text clearly. If you need assistance with reading text in an image, please provide a clearer
generated_text  The image is too blurry to read the text clearly. If you need assistance with reading text in an image, please provide a clearer
task-l_pphwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the OfficerNumber written in the image? [/INST] The image is too blurry to read the text clearly. If you need assistance with something else, feel free to ask! 
generated_text  The image is too blurry to read the text clearly. If you need assistance with something else, feel free to ask! 
task-doc_vqa


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the OfficerNumber written in the image? [/INST] The OfficerNumber written in the image is 9295. 
generated_text  The OfficerNumber written in the image is 9295. 
task-bb
[INST]  
what is the bounding box for OfficerNumberin the image? Answer the question using a single word or phrase. [/INST] 0.000,0.000,0.
generated_text  0.000,0.000,0.
[{'time_vqa': ' 1 day ', 'bail_vqa': ' Non-bailable ', 'time_qs': '[INST] <image>\nWhat is the difference in time between the occurrence of the event and when it was reported? Answer the question using a single word or phrase. [/INST]', 'bail_qs': '[INST] <image>\nAre the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Answer the question using a single word or phrase. [/INST]', 'image_name': '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg', 'time_gt': '', 'bail_gt': ''}, {'time_vqa': ' 1 day ', 'bail_v

**30 Image subset**

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
data = data[:30]
evaluated_data = []
model_name = "llava-v1.6-mistral-7b-hf"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt = "[INST] <image>\n"+ qs +  " [/INST]"

    label_name = d["label_name"]
    label_qs = "[INST] <image>\n"+"what is the " + label_name + " written in the image?"+  " [/INST]"
    print("question", qs)

    bb_qs = "[INST] <image>\n"+"what is the bounding box for " + label_name + "in the image?"+  " Answer the question using a single word or phrase."+ " [/INST]"

    time_qs = "[INST] <image>\n"+"What is the difference in time between the occurrence of the event and when it was reported?"+  " Answer the question using a single word or phrase."+" [/INST]"

    bail_qs = "[INST] <image>\n"+"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Answer the question using a single word or phrase."+" [/INST]"

    print("task-hwr")
    hwr = llava_next(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = llava_next(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = llava_next(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = llava_next(label_qs,hwr_image)
    print("task-l_phwr")
    l_phwr = llava_next(label_qs,p_img)
    print("task-l_pphwr")
    l_pphwr = llava_next(label_qs,pp_img)
    print("task-doc_vqa")
    doc_vqa = llava_next(label_qs,full_img)
    print("task-bb")
    bb_vqa = llava_next(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = llava_next(time_qs,full_img,max_length= 300)
      print("task-bail")
      bail_vqa = llava_next(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-30"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-30"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


question what is written in the image? Answer the question using a single word or phrase.
task-hwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is written in the image? Answer the question using a single word or phrase. [/INST] Airplane 
generated_text  Airplane 
task-phwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

[INST]  
what is the Date written in the image? [/INST] The date written in the image is "0718." 
generated_text  The date written in the image is "0718." 
task-l_pphwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the Date written in the image? [/INST] The image shows a date written in a cursive script. It appears to be "07 18," which could be interpreted as
generated_text  The image shows a date written in a cursive script. It appears to be "07 18," which could be interpreted as
task-doc_vqa


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the Date written in the image? [/INST] The date written in the image is "01/18/2018." 
generated_text  The date written in the image is "01/18/2018." 
task-bb
[INST]  
what is the bounding box for Datein the image? Answer the question using a single word or phrase. [/INST] [0.000,0.000,0.998,0.988] 
generated_text  [0.000,0.000,0.998,0.988] 
[{'time_vqa': ' 1 day ', 'bail_vqa': ' Non-bailable ', 'time_qs': '[INST] <image>\nWhat is the difference in time between the occurrence of the event and when it was reported? Answer the question using a single word or phrase. [/INST]', 'bail_qs': '[INST] <image>\nAre the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Answer the question using a single word or phrase. [/INST]', 'image_name': '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg', 'time_gt': '', 'bail_gt': ''}, {'time_vqa': ' 1 day ', 'ba

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
#

img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)
evaluated_data = []
model_name = "llava-v1.6-mistral-7b-hf"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []


for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    hwr_image = Image.open(img_path).convert("RGB")
    p_img = Image.open(p_img_path).convert("RGB")
    pp_img = Image.open(pp_img_path).convert("RGB")
    full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    hwr_prompt = "[INST] <image>\n"+ qs +  " [/INST]"

    label_name = d["label_name"]
    label_qs = "[INST] <image>\n"+"what is the " + label_name + " written in the image?"+  " [/INST]"
    print("question", qs)

    bb_qs = "[INST] <image>\n"+"what is the bounding box for " + label_name + "in the image?"+  " Answer the question using a single word or phrase."+ " [/INST]"

    time_qs = "[INST] <image>\n"+"What is the difference in time between the occurrence of the event and when it was reported?"+  " Answer the question using a single word or phrase."+" [/INST]"

    bail_qs = "[INST] <image>\n"+"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Answer the question using a single word or phrase."+" [/INST]"

    print("task-hwr")
    hwr = llava_next(hwr_prompt,hwr_image)
    print("task-phwr")
    phwr = llava_next(hwr_prompt,p_img)
    print("task-pphwr")
    pphwr = llava_next(hwr_prompt,pp_img)
    print("task-l_hwr")
    l_hwr = llava_next(label_qs,hwr_image)
    print("task-l_phwr")
    l_phwr = llava_next(label_qs,p_img)
    print("task-l_pphwr")
    l_pphwr = llava_next(label_qs,pp_img)
    print("task-doc_vqa")
    doc_vqa = llava_next(label_qs,full_img)
    print("task-bb")
    bb_vqa = llava_next(bb_qs,full_img,max_length= 100)


    if full_img not in unique_image_list:
      print("task-time")
      time_vqa = llava_next(time_qs,full_img,max_length= 300)
      print("task-bail")
      bail_vqa = llava_next(bail_qs,full_img,max_length= 100)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":full_img_path,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(full_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


question what is written in the image? Answer the question using a single word or phrase.
task-hwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is written in the image? Answer the question using a single word or phrase. [/INST] Airplane 
generated_text  Airplane 
task-phwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

[INST]  
what is the Date written in the image? [/INST] The date written in the image is "03 10 07 17." 
generated_text  The date written in the image is "03 10 07 17." 
task-l_pphwr


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the Date written in the image? [/INST] The date written in the image is "03 10 17." 
generated_text  The date written in the image is "03 10 17." 
task-doc_vqa


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]  
what is the Date written in the image? [/INST] The date written in the image is "03/17/2017." 
generated_text  The date written in the image is "03/17/2017." 
task-bb
[INST]  
what is the bounding box for Datein the image? Answer the question using a single word or phrase. [/INST] 0.197,0.000,0.998,0.988 
generated_text  0.197,0.000,0.998,0.988 
[{'time_vqa': ' 1 day ', 'bail_vqa': ' Non-bailable ', 'time_qs': '[INST] <image>\nWhat is the difference in time between the occurrence of the event and when it was reported? Answer the question using a single word or phrase. [/INST]', 'bail_qs': '[INST] <image>\nAre the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Answer the question using a single word or phrase. [/INST]', 'image_name': '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg', 'time_gt': '', 'bail_gt': ''}, {'time_vqa': ' 1 day ', 'bail_v

**HWR-PAD10**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
data = data[:10]
evaluated_data = []
model_name = "Monkey-pad10"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 10)
    pad_img.save(padded_path)

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    prompt = "[INST] <image>\n"+ qs +  " [/INST]"
    inputs = processor(text=prompt, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

**HWR-PAD20**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "llava-v1.6-mistral-7b-hf-pad20"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 20)
    pad_img.save(padded_path)

    qs = d['question']
    qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    prompt = "[INST] <image>\n"+ qs +  " [/INST]"
    inputs = processor(text=prompt, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

LLAVA-NEXT LabelName

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-labelname"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)


    inputs = processor(text=qs, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

LabelName-Pad10

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-label-pad10"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])


    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)


    # pad_img = image_padding(image,pad_size = 10)
    # pad_img.save(padded_path)

    # qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    inputs = processor(text=query, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

**LabelName-Pad20**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-label-pad20"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])


    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)


    # pad_img = image_padding(image,pad_size = 10)
    # pad_img.save(padded_path)

    # qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    inputs = processor(text=query, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

**DocVQA-LLAVANEXT**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-docvqa"

# out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    # img_path = os.path.join(image_folder, d['image_path'])
    img_path = os.path.join(image_folder, d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg")
    print(img_path)
    image = Image.open(img_path).convert("RGB")

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    inputs = processor(text=query, images=image, return_tensors="pt")

    # Generate
    generate_ids = model.generate(**inputs, max_length=50)
    print(processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0])
    generated_text = processor.batch_decode(generate_ids, skip_special_tokens=True, clean_up_tokenization_spaces=False)[0]
    final_output = generated_text.split("[/INST]")[1]
    print("generated_text",final_output)
    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(final_output, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = final_output
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

In [ ]:
import torch

with torch.no_grad():
    outputs = model(**inputs)
logits = outputs.logits
print(logits.shape)



In [ ]:
texts = [ground_truth]

In [ ]:
import matplotlib.pyplot as plt

logits = logits.unsqueeze(1)
print(logits.shape)


In [ ]:
_, ax = plt.subplots(1, len(texts) + 1, figsize=(100*(len(texts) + 1), 1))
[a.axis('off') for a in ax.flatten()]
ax[0].imshow(image)
[ax[i+1].imshow(torch.sigmoid(logits[i][0])) for i in range(len(texts))];
[ax[i+1].text(0, -15, prompt) for i, prompt in enumerate(texts)];
print("model prediction",final_output)

In [ ]:
generate_ids

### **Monkey**

In [ ]:
!pip install peft

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.6/251.6 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 37.0 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-many

In [ ]:
!pip install transformers_stream_generator einops

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 2.1 MB/s eta 0:00:00
  Created wheel for transformers_stream_generator: filename=transformers_stream_generator-0.0.5-py3-none-any.whl size=12425 sha256=50a27e5c6bb3f760c9d80d3337f7d565aa07c5b784e94386dbc7134c43b37f9b
  Stored in directory: /root/.cache/pip/wheels/95/4a/90/140f7b67d125906f6a165f38aad212ecb4a695ad0d87582437
Successfully built transformers_stream_generator


In [ ]:
!pip install tiktoken

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 21.6 MB/s eta 0:00:00


In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 53.8 MB/s eta 0:00:00


In [ ]:
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

from transformers import AutoModelForCausalLM, AutoTokenizer

checkpoint = "echo840/Monkey"
model = AutoModelForCausalLM.from_pretrained(checkpoint, device_map='cuda', trust_remote_code=True).eval()
tokenizer = AutoTokenizer.from_pretrained(checkpoint, trust_remote_code=True)
tokenizer.padding_side = 'left'
tokenizer.pad_token_id = tokenizer.eod_id

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.17k [00:00<?, ?B/s]

configuration_qwen.py:   0%|          | 0.00/2.09k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/echo840/Monkey:
- configuration_qwen.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


modeling_monkey.py:   0%|          | 0.00/6.17k [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/288 [00:00<?, ?B/s]

tokenization_qwen.py:   0%|          | 0.00/21.3k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/echo840/Monkey:
- tokenization_qwen.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


qwen.tiktoken:   0%|          | 0.00/2.56M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/35.0 [00:00<?, ?B/s]

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")


    qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

In [ ]:
def monkey_model(query,max_new_tokens=512):

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=max_new_tokens,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)
    return response

**25-Sample-Evaluation**

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "Monkey"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']
    #qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    p_hwr_prompt = f'<img>{p_img_path}</img> {qs} Answer: ' #VQA
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA

    label_name = d["label_name"]
    label_qs = f"<img>{img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"
    print("question", qs)
    p_label_qs = f"<img>{p_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"
    pp_label_qs = f"<img>{pp_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"

    docvqa_qs = f"<img>{full_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"


    bb_qs = f"<img>{full_img_path}</img>"+"what is the bounding box for " + label_name + "in the image?"+  " Answer :"


    time_qs = f"<img>{full_img_path}</img>"+"What is the difference in time between the occurrence of the event and when it was reported?"+  " Short Answer:"

    bail_qs = f"<img>{full_img_path}</img>"+"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Short Answer:"

    print("task-hwr")
    hwr = monkey_model(hwr_prompt)
    print("task-phwr")
    phwr = monkey_model(p_hwr_prompt)
    print("task-pphwr")
    pphwr = monkey_model(pp_hwr_prompt)
    print("task-l_hwr")
    l_hwr = monkey_model(label_qs)
    print("task-l_phwr")
    l_phwr = monkey_model(p_label_qs)
    print("task-l_pphwr")
    l_pphwr = monkey_model(pp_label_qs)
    print("task-doc_vqa")
    doc_vqa = monkey_model(docvqa_qs)
    print("task-bb")
    bb_vqa = monkey_model(bb_qs)


    if root_img not in unique_image_list:
      print("task-time")
      time_vqa = monkey_model(time_qs)
      print("task-bail")
      bail_vqa = monkey_model(bail_qs)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(root_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
# LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25-V2"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image?
task-time
1200 Hrs
task-bail
bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
08.31.18
task-bail
bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
13Hrs
task-bail
bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
12 Hrs
task-bail
bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
12 Hrs
task-bail
bailabl

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 100):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "Monkey"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']
    #qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    p_hwr_prompt = f'<img>{p_img_path}</img> {qs} Answer: ' #VQA
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA

    label_name = d["label_name"]
    label_qs = f"<img>{img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"
    print("question", qs)
    p_label_qs = f"<img>{p_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"
    pp_label_qs = f"<img>{pp_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"

    docvqa_qs = f"<img>{full_img_path}</img>"+"what is the " + label_name + " written in the image?"+  "Answer:"


    bb_qs = f"<img>{full_img_path}</img>"+"what is the bounding box for " + label_name + "in the image?"+  " Answer :"


    time_qs = f"<img>{full_img_path}</img>"+"What is the difference in time between the occurrence of the event and when it was reported?"+  " Short Answer:"

    bail_qs = f"<img>{full_img_path}</img>"+"""Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""+  " Short Answer with explaination:"

    # print("task-hwr")
    # hwr = monkey_model(hwr_prompt)
    # print("task-phwr")
    # phwr = monkey_model(p_hwr_prompt)
    # print("task-pphwr")
    # pphwr = monkey_model(pp_hwr_prompt)
    # print("task-l_hwr")
    # l_hwr = monkey_model(label_qs)
    # print("task-l_phwr")
    # l_phwr = monkey_model(p_label_qs)
    # print("task-l_pphwr")
    # l_pphwr = monkey_model(pp_label_qs)
    # print("task-doc_vqa")
    # doc_vqa = monkey_model(docvqa_qs)
    # print("task-bb")
    # bb_vqa = monkey_model(bb_qs)


    if root_img not in unique_image_list:
      print("task-time")
      time_vqa = monkey_model(time_qs)
      print("task-bail")
      bail_vqa = monkey_model(bail_qs)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(root_img)



    ## evaluation
    # ground_truth = d["answers"]

    # try:
    #   hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    # except:
    #   hwr_cer_error, hwr_wer_error = 100,100

    # try:
    #   phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    # except:
    #   phwr_cer_error, phwr_wer_error = 100,100

    # try:
    #   pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    # except:
    #   pphwr_cer_error, pphwr_wer_error = 100,100

    # try:
    #   l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    # except:
    #   l_hwr_cer_error, l_hwr_wer_error = 100,100

    # try:
    #   l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    # except:
    #   l_phwr_cer_error, l_phwr_wer_error = 100,100

    # try:
    #   l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    # except:
    #   l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    # try:
    #   doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    # except:
    #   doc_vqa_cer_error, doc_vqawer_error = 100,100

    # d["hwr_cer"] = hwr_cer_error
    # d["hwr_wer"] = hwr_wer_error
    # d["hwr_model_output"] = hwr
    # d["hwr_prompt"] = hwr_prompt

    # d["phwr_cer"] = phwr_cer_error
    # d["phwr_wer"] = phwr_wer_error
    # d["phwr_model_output"] = phwr
    # d["phwr_prompt"] = hwr_prompt

    # d["pphwr_cer"] = pphwr_cer_error
    # d["pphwr_wer"] = pphwr_wer_error
    # d["pphwr_model_output"] = pphwr
    # d["pphwr_prompt"] = hwr_prompt

    # d["l_hwr_cer"] = l_hwr_cer_error
    # d["l_hwr_wer"] = l_hwr_wer_error
    # d["l_hwr_model_output"] = l_hwr
    # d["l_hwr_prompt"] = label_qs

    # d["l_phwr_cer"] = l_phwr_cer_error
    # d["l_phwr_wer"] = l_phwr_wer_error
    # d["l_phwr_model_output"] = l_phwr
    # d["l_phwr_hwr_prompt"] = label_qs

    # d["l_pphwr_cer"] = l_pphwr_cer_error
    # d["l_pphwr_wer"] = l_pphwr_wer_error
    # d["l_pphwr_model_output"] = l_pphwr
    # d["l_pphwr_hwr_prompt"] = label_qs

    # d["doc_vqa_cer"] = doc_vqa_cer_error
    # d["doc_vqa_wer"] = doc_vqa_wer_error
    # d["doc_vqa_model_output"] = doc_vqa
    # d["doc_vqa_hwr_prompt"] = label_qs



    # d["bbox_model_output"] = bb_vqa
    # d["bbox_hwr_prompt"] = bb_qs

    # d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
# with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
#     json.dump(evaluated_data, outfile)

print(LRVQA)
# LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-100-explaination"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image?
task-time
1200 Hrs
task-bail
Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
08.31.18
task-bail
bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
13Hrs
task-bail
Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
12 Hrs
task-bail
Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
12 Hrs
task-bail
Bailabl

In [ ]:
import json
import os

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"

with open(data_path, "r") as f:
    data = json.load(f)

In [ ]:
img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)





print(img_count)
print(filt_data)
print(len(filt_data))

{'Airport PSAIRPORT-0019-2018-1020__1.jpg': ['Airport PSAIRPORT-0019-2018-1020__1.jpg', 'Airport PSAIRPORT-0019-2018-1020__1.jpg', 'Airport PSAIRPORT-0019-2018-1020__1.jpg', 'Airport PSAIRPORT-0019-2018-1020__1.jpg', 'Airport PSAIRPORT-0019-2018-1020__1.jpg'], 'Airport PSAIRPORT-0007-2018-1932__1.jpg': ['Airport PSAIRPORT-0007-2018-1932__1.jpg', 'Airport PSAIRPORT-0007-2018-1932__1.jpg', 'Airport PSAIRPORT-0007-2018-1932__1.jpg', 'Airport PSAIRPORT-0007-2018-1932__1.jpg', 'Airport PSAIRPORT-0007-2018-1932__1.jpg'], 'Airport PSAIRPORT-0013-2018-3843__1.jpg': ['Airport PSAIRPORT-0013-2018-3843__1.jpg', 'Airport PSAIRPORT-0013-2018-3843__1.jpg', 'Airport PSAIRPORT-0013-2018-3843__1.jpg', 'Airport PSAIRPORT-0013-2018-3843__1.jpg', 'Airport PSAIRPORT-0013-2018-3843__1.jpg'], 'Baguiati PS513-19__1.jpg': ['Baguiati PS513-19__1.jpg', 'Baguiati PS513-19__1.jpg', 'Baguiati PS513-19__1.jpg', 'Baguiati PS513-19__1.jpg', 'Baguiati PS513-19__1.jpg'], 'Bidhannagar South PSBDN-SOUTH-0119-2017-8072__1.

In [ ]:
list(set(labels))

['Date', 'Subdivision', 'FirNum', 'Dist', 'Year', 'Sections', 'PoliceStation']

In [ ]:
image_list = [d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg" for d in data ]
img_list = list(set(image_list))
print(len(img_list))

11


In [ ]:
img_list

['Airport PSAIRPORT-0019-2018-1020__1.jpg',
 'ECO PARK PS03__1.jpg',
 'ECO PARK PS26__1.jpg',
 'Bidhannagar South PSBDN-SOUTH-0119-2017-8072__1.jpg',
 'Bidhannagar North PSBDN-NORTH-0224-2017-5429__1.jpg',
 'Airport PSAIRPORT-0007-2018-1932__1.jpg',
 'Airport PSAIRPORT-0013-2018-3843__1.jpg',
 'Baguiati PS513-19__1.jpg',
 'ECO PARK PS34__1.jpg',
 'Bidhannagar North PSBDN-NORTH-0244-2017-4806__1.jpg',
 'Women PSWOMEN-0025-2017-3083__1.jpg']

**HWR-PAD10**

In [ ]:
def image_padding(image,pad_size = 10):
  right = pad_size
  left = pad_size
  top = pad_size
  bottom = pad_size

  width, height = image.size

  new_width = width + right + left
  new_height = height + top + bottom

  result = Image.new(image.mode, (new_width, new_height), (255, 255, 255))

  result.paste(image, (left, top))

  return result

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
data = data[:10]
evaluated_data = []
model_name = "Monkey-pad10"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 10)
    pad_img.save(padded_path)

    qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

resilience
2018
islam
2013
1481481333543759
6/3
apc
lost
unanswerable
unanswerable
Overall CER 0.8336507936507938
Overall WER 0.9


**HWR-PAD20**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-pad20"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 20)
    pad_img.save(padded_path)

    qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

unanswerable
2018
islla
02-02-2013
14812313544379
50 6/3
s p e
lost
unanswerable
unanswerable
e=mc2
123456789
unanswerable
formant: ashma xhatoom
ondeljana
KPI-7003F
attached here
1471383235412758
29 i glpe
peronanta barone
head of the office in charge police station with
act like your parents
Aloper
ant commissioned
cfr
bargain
alpen
2018
0718
happy
250938
373
28.15
sunday
아침
21.15
아니야
23
alamkar
Babu Sardar
trench
reproduse belea
2f93381pc
s r l maurice
police
moham lad ghouse
for all
unanswerable
army
micicdonherp
the impulsive bn
happy new year
2018
1918
1918
2991399
911
at 18:15 hwy
solaris
it is my
19418
911
approxx
azizul haque tarafgar
guud
Attached herewith
279/338 I Pe
s l a m y p a l
police
police
19-01-18
unanswerable
24 pgs in
batesat
bogu
2019
513
16-12-19
ipc
2pi / 938.479
1962
2135
icte219
16.30
16/12/15
alamout 253
1362
Erajul Jarofdar
4 'habibur tarofder
ghillie
673-25+196
q 29 33 8 42 9 tpc
unanswerable
scottish whisky as 1831
unanswerable
e.j. fur tarebber
dwg
DNF
w

**Monkey LabelName**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-labelname"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

question what is the PoliceStation written in the image?
police station
question what is the Year written in the image?
2018
question what is the FirNum written in the image?
12345
question what is the Date written in the image?
2015
question what is the Sections written in the image?
1984
question what is the OtherActs written in the image?
Other Acts
question what is the Sections written in the image?
1986 Act
question what is the GDEntNum written in the image?
123456789
question what is the GDTime written in the image?
10:10
question what is the ReceivedDate written in the image?
2015-03-13
question what is the OOODate written in the image?
2015-03-01
question what is the ReceivedTime written in the image?
2019-03-13T16:40:00.000+0000
question what is the GDNumber written in the image?
10
question what is the CompName written in the image?
KOMPAK
question what is the Nationality written in the image?
American
question what is the CompAddress written in the image?
123456789
question 

**Monkey-LabelName-Pad10**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-label-pad10"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])


    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)


    # pad_img = image_padding(image,pad_size = 10)
    # pad_img.save(padded_path)

    # qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

question what is the PoliceStation written in the image?
police station
question what is the Year written in the image?
2018
question what is the FirNum written in the image?
12113
question what is the Date written in the image?
2013
question what is the Sections written in the image?
148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 222, 223, 224, 225, 226, 227, 228, 229, 230, 231, 232, 233, 234, 235, 236, 237, 238, 239, 240, 241, 242, 243, 244, 245, 246, 247, 248, 249, 25
question what is the OtherActs written in the image?
6/3/19
question what is the Sections written in the image?
a, b, c, d, e, f, g, h, i, j, k, l, m, n, o, p, q, r, s, t, u, v, w, x, y, z
question wha

**Monkey-labelname-pad20**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-label-pad20"

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"

total_cer =0
total_wer =0
avg_count =0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")

    padded_path = os.path.join(out_folder,d['image_path'])


    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)


    # pad_img = image_padding(image,pad_size = 10)
    # pad_img.save(padded_path)

    # qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{padded_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

question what is the PoliceStation written in the image?
police station
question what is the Year written in the image?
2018
question what is the FirNum written in the image?
123456789
question what is the Date written in the image?
02-02-2013
question what is the Sections written in the image?
148, 231, 354, 437
question what is the OtherActs written in the image?
50/6/3
question what is the Sections written in the image?
SPE
question what is the GDEntNum written in the image?
1024
question what is the GDTime written in the image?
10:10
question what is the ReceivedDate written in the image?
Mon, 17 Sep 2012 14:10:03 +0200
question what is the OOODate written in the image?
2015-03-04
question what is the ReceivedTime written in the image?
12:25:45
question what is the GDNumber written in the image?
10
question what is the CompName written in the image?
formant
question what is the Nationality written in the image?
American
question what is the CompAddress written in the image?
www.com

**document question answer- monkey**

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:10]
evaluated_data = []
model_name = "Monkey-docvqa"

# out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"

total_cer =0
total_wer =0
avg_count =0

for d in data:
    # print("Data",data[i])
    # img_path = os.path.join(image_folder, d['image_path'])
    img_path = os.path.join(image_folder, d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg")
    print(img_path)
    image = Image.open(img_path).convert("RGB")

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    query = f'<img>{img_path}</img> {qs} Answer: ' #VQA
    # query = f'<img>{img_path}</img> Generate the detailed caption in English: ' #detailed caption

    input_ids = tokenizer(query, return_tensors='pt', padding='longest')
    attention_mask = input_ids.attention_mask
    input_ids = input_ids.input_ids

    pred = model.generate(
                input_ids=input_ids.cuda(),
                attention_mask=attention_mask.cuda(),
                do_sample=False,
                num_beams=1,
                max_new_tokens=512,
                min_new_tokens=1,
                length_penalty=1,
                num_return_sequences=1,
                output_hidden_states=True,
                use_cache=True,
                pad_token_id=tokenizer.eod_id,
                eos_token_id=tokenizer.eod_id,
                )
    response = tokenizer.decode(pred[0][input_ids.size(1):].cpu(), skip_special_tokens=True).strip()
    print(response)

    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(response, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = response
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the PoliceStation written in the image?
POLICE STATION
/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Year written in the image?
2017
/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the FirNum written in the image?
151/2017
/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Date written in the image?
10.2.18
/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Sections written in the image?
184
/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the OtherActs written

### **internlm/internlm-xcomposer-7b**

### **Qwen**

In [ ]:
!pip install accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 6.4 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-m

In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 6.1 MB/s eta 0:00:00


In [ ]:
!pip install tiktoken

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 9.5 MB/s eta 0:00:00


In [ ]:
!pip install transformers_stream_generator einops

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 2.6 MB/s eta 0:00:00
  Created wheel for transformers_stream_generator: filename=transformers_stream_generator-0.0.5-py3-none-any.whl size=12425 sha256=f554321ba6b2d86173fde26b3801657e016676848880db52a3014fff674c9551
  Stored in directory: /root/.cache/pip/wheels/95/4a/90/140f7b67d125906f6a165f38aad212ecb4a695ad0d87582437
Successfully built transformers_stream_generator


In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from transformers.generation import GenerationConfig
import torch
torch.manual_seed(1234)

tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen-VL", trust_remote_code=True)

# use bf16
# model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen-VL", device_map="auto", trust_remote_code=True, bf16=True).eval()
# use fp16
# model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen-VL", device_map="auto", trust_remote_code=True, fp16=True).eval()
# use cpu only
# model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen-VL", device_map="cpu", trust_remote_code=True).eval()
# use cuda device
model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen-VL", device_map="cuda", trust_remote_code=True).eval()

# Specify hyperparameters for generation (No need to do this if you are using transformers>=4.32.0)
# model.generation_config = GenerationConfig.from_pretrained("Qwen/Qwen-VL", trust_remote_code=True)




/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/173 [00:00<?, ?B/s]

tokenization_qwen.py:   0%|          | 0.00/21.9k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/Qwen/Qwen-VL:
- tokenization_qwen.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


qwen.tiktoken:   0%|          | 0.00/2.56M [00:00<?, ?B/s]

...

pytorch_model-00008-of-00010.bin:   0%|          | 0.00/1.98G [00:00<?, ?B/s]

pytorch_model-00009-of-00010.bin:   0%|          | 0.00/1.99G [00:00<?, ?B/s]

pytorch_model-00010-of-00010.bin:   0%|          | 0.00/1.73G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/10 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/218 [00:00<?, ?B/s]

In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

data = data[:10]
evaluated_data = []
model_name = "Qwen-VL"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])
    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
#   with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
#       json.dump(evaluated_data, outfile)


 abracadabra
 unanswerable
 jiskha
 1234567890
 teifotou teifotou
 unanswerable
 pc
 pi
 1234567890
 zollicoffer


**25-Sample-Evalulation**

In [ ]:
def qwenvl(query):
    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    return generated_text

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"


data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"
annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "QWEN-VL"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']

    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])

    #qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'{qs} Answer: ' #VQA
    hwr_prompt1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},])
    p_hwr_prompt = f'{qs} Answer: ' #VQA
    p_hwr_prompt1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{qs} Answer:'},])
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA
    pp_hwr_prompt1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{qs} Answer:'},])

    label_name = d["label_name"]
    label_qs = "what is the " + label_name + "written in the image?"
    label_qs1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{label_qs} Answer:'},])
    print("question", qs)
    p_label_qs = "what is the " + label_name + " written in the image?"
    p_label_qs1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{p_label_qs} Answer:'},])

    pp_label_qs = "what is the " + label_name + " written in the image?"
    pp_label_qs1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{pp_label_qs} Answer:'},])

    docvqa_qs = "what is the " + label_name + " written in the image?"
    docvqa_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{docvqa_qs} Answer:'},])

    bb_qs = "what is the bounding box for " + label_name + "in the image?"
    bb_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bb_qs} Answer:'},])

    time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"
    time_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{time_qs} Answer:'},])
    bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""
    bail_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bail_qs} Answer:'},])

    print("task-hwr")
    hwr = qwenvl(hwr_prompt1)
    print("task-phwr")
    phwr = qwenvl(p_hwr_prompt1)
    print("task-pphwr")
    pphwr = qwenvl(pp_hwr_prompt1)
    print("task-l_hwr")
    l_hwr = qwenvl(label_qs1)
    print("task-l_phwr")
    l_phwr = qwenvl(p_label_qs1)
    print("task-l_pphwr")
    l_pphwr = qwenvl(pp_label_qs1)
    print("task-doc_vqa")
    doc_vqa = qwenvl(docvqa_qs1)
    print("task-bb")
    bb_vqa = qwenvl(bb_qs1)


    if root_img not in unique_image_list:
      print("task-time")
      time_vqa = qwenvl(time_qs1)
      print("task-bail")
      bail_vqa = qwenvl(bail_qs1)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(root_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    try:
      l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    except:
      l_hwr_cer_error, l_hwr_wer_error = 100,100

    try:
      l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    except:
      l_phwr_cer_error, l_phwr_wer_error = 100,100

    try:
      l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    except:
      l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    try:
      doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    except:
      doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    d["l_hwr_cer"] = l_hwr_cer_error
    d["l_hwr_wer"] = l_hwr_wer_error
    d["l_hwr_model_output"] = l_hwr
    d["l_hwr_prompt"] = label_qs

    d["l_phwr_cer"] = l_phwr_cer_error
    d["l_phwr_wer"] = l_phwr_wer_error
    d["l_phwr_model_output"] = l_phwr
    d["l_phwr_hwr_prompt"] = label_qs

    d["l_pphwr_cer"] = l_pphwr_cer_error
    d["l_pphwr_wer"] = l_pphwr_wer_error
    d["l_pphwr_model_output"] = l_pphwr
    d["l_pphwr_hwr_prompt"] = label_qs

    d["doc_vqa_cer"] = doc_vqa_cer_error
    d["doc_vqa_wer"] = doc_vqa_wer_error
    d["doc_vqa_model_output"] = doc_vqa
    d["doc_vqa_hwr_prompt"] = label_qs



    d["bbox_model_output"] = bb_vqa
    d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)

print(LRVQA)
# LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25-V2"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image?
task-hwr
 beethoven 154
task-phwr
 tequila 1944
task-pphwr
 hippon
task-l_hwr
 btp
task-l_phwr
 134
task-l_pphwr
 134
task-doc_vqa
 AUSTRALIA
task-bb
 BRIDGETOWN POLICE STATION
task-time
 72 Hours
task-bail
 Bailable
question what is written in the image?
task-hwr
 lo res
task-phwr
 loleilove
task-pphwr
 12:27
task-l_hwr
 1987
task-l_phwr
 2018
task-l_pphwr
 2018
task-doc_vqa
 2015
task-bb
 0-2
question what is written in the image?
task-hwr
 jiskha
task-phwr
 j5113
task-pphwr
 islla
task-l_hwr
 72453
task-l_phwr
 15113
task-l_pphwr
 jolla
task-doc_vqa
 15-2418
task-bb
 268-270
question what is written in the image?
task-hwr
 032013
task-phwr
 02-02-2013
task-pphwr
 02.02.2013
task-l_hwr
 24-02-2013
task-l_phwr
 02-03-2013
task-l_pphwr
 02-02-2013
task-doc_vqa
 13/2/1982
task-bb
 117,213),(224,257)
question what is written in the image?
task-hwr
 help
task-phwr
 123456789123456789
task-pphwr
 pi
task-l_hwr
 1987
task-l_phwr
 1481378323854379
task-

**Legal-Evaluation**

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 100):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "QWEN-VL"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']

    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])

    #qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'{qs} Answer: ' #VQA
    hwr_prompt1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},])
    p_hwr_prompt = f'{qs} Answer: ' #VQA
    p_hwr_prompt1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{qs} Answer:'},])
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA
    pp_hwr_prompt1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{qs} Answer:'},])

    label_name = d["label_name"]
    label_qs = "what is the " + label_name + "written in the image?"
    label_qs1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{label_qs} Answer:'},])
    print("question", qs)
    p_label_qs = "what is the " + label_name + " written in the image?"
    p_label_qs1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{p_label_qs} Answer:'},])

    pp_label_qs = "what is the " + label_name + " written in the image?"
    pp_label_qs1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{pp_label_qs} Answer:'},])

    docvqa_qs = "what is the " + label_name + " written in the image?"
    docvqa_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{docvqa_qs} Answer:'},])

    bb_qs = "what is the bounding box for " + label_name + "in the image?"
    bb_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bb_qs} Answer:'},])

    time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"
    time_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{time_qs} Answer:'},])
    bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Provide Reason."""
    bail_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bail_qs} Answer:'},])

    # print("task-hwr")
    # hwr = qwenvl(hwr_prompt1)
    # print("task-phwr")
    # phwr = qwenvl(p_hwr_prompt1)
    # print("task-pphwr")
    # pphwr = qwenvl(pp_hwr_prompt1)
    # print("task-l_hwr")
    # l_hwr = qwenvl(label_qs1)
    # print("task-l_phwr")
    # l_phwr = qwenvl(p_label_qs1)
    # print("task-l_pphwr")
    # l_pphwr = qwenvl(pp_label_qs1)
    # print("task-doc_vqa")
    # doc_vqa = qwenvl(docvqa_qs1)
    # print("task-bb")
    # bb_vqa = qwenvl(bb_qs1)


    if root_img not in unique_image_list:
      print("task-time")
      time_vqa = qwenvl(time_qs1)
      print("task-bail")
      bail_vqa = qwenvl(bail_qs1)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(root_img)



    ## evaluation
    ground_truth = d["answers"]

    # try:
    #   hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    # except:
    #   hwr_cer_error, hwr_wer_error = 100,100

    # try:
    #   phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    # except:
    #   phwr_cer_error, phwr_wer_error = 100,100

    # try:
    #   pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    # except:
    #   pphwr_cer_error, pphwr_wer_error = 100,100

    # try:
    #   l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    # except:
    #   l_hwr_cer_error, l_hwr_wer_error = 100,100

    # try:
    #   l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    # except:
    #   l_phwr_cer_error, l_phwr_wer_error = 100,100

    # try:
    #   l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    # except:
    #   l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    # try:
    #   doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    # except:
    #   doc_vqa_cer_error, doc_vqawer_error = 100,100

    # d["hwr_cer"] = hwr_cer_error
    # d["hwr_wer"] = hwr_wer_error
    # d["hwr_model_output"] = hwr
    # d["hwr_prompt"] = hwr_prompt

    # d["phwr_cer"] = phwr_cer_error
    # d["phwr_wer"] = phwr_wer_error
    # d["phwr_model_output"] = phwr
    # d["phwr_prompt"] = hwr_prompt

    # d["pphwr_cer"] = pphwr_cer_error
    # d["pphwr_wer"] = pphwr_wer_error
    # d["pphwr_model_output"] = pphwr
    # d["pphwr_prompt"] = hwr_prompt

    # d["l_hwr_cer"] = l_hwr_cer_error
    # d["l_hwr_wer"] = l_hwr_wer_error
    # d["l_hwr_model_output"] = l_hwr
    # d["l_hwr_prompt"] = label_qs

    # d["l_phwr_cer"] = l_phwr_cer_error
    # d["l_phwr_wer"] = l_phwr_wer_error
    # d["l_phwr_model_output"] = l_phwr
    # d["l_phwr_hwr_prompt"] = label_qs

    # d["l_pphwr_cer"] = l_pphwr_cer_error
    # d["l_pphwr_wer"] = l_pphwr_wer_error
    # d["l_pphwr_model_output"] = l_pphwr
    # d["l_pphwr_hwr_prompt"] = label_qs

    # d["doc_vqa_cer"] = doc_vqa_cer_error
    # d["doc_vqa_wer"] = doc_vqa_wer_error
    # d["doc_vqa_model_output"] = doc_vqa
    # d["doc_vqa_hwr_prompt"] = label_qs



    # d["bbox_model_output"] = bb_vqa
    # d["bbox_hwr_prompt"] = bb_qs

    # d["model_name"] = model_name

    # evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
# with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
#     json.dump(evaluated_data, outfile)

print(LRVQA)
# LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-100"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image?
task-time
 121 hours
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 18 months
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 18 Hrs, 55 Mins
task-bail
 bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 23.55 Hrs
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 100):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "QWEN-VL"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']

    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])

    #qs = qs+" Answer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"
    # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'{qs} Answer: ' #VQA
    hwr_prompt1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},])
    p_hwr_prompt = f'{qs} Answer: ' #VQA
    p_hwr_prompt1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{qs} Answer:'},])
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA
    pp_hwr_prompt1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{qs} Answer:'},])

    label_name = d["label_name"]
    label_qs = "what is the " + label_name + "written in the image?"
    label_qs1 = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{label_qs} Answer:'},])
    print("question", qs)
    p_label_qs = "what is the " + label_name + " written in the image?"
    p_label_qs1 = tokenizer.from_list_format([
        {'image': p_img_path},
        {'text': f'<img>{p_img_path}</img>{p_label_qs} Answer:'},])

    pp_label_qs = "what is the " + label_name + " written in the image?"
    pp_label_qs1 = tokenizer.from_list_format([
        {'image': pp_img_path},
        {'text': f'<img>{pp_img_path}</img>{pp_label_qs} Answer:'},])

    docvqa_qs = "what is the " + label_name + " written in the image?"
    docvqa_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{docvqa_qs} Answer:'},])

    bb_qs = "what is the bounding box for " + label_name + "in the image?"
    bb_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bb_qs} Answer:'},])

    time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"
    time_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{time_qs} Answer:'},])
    bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable". Provide explaination."""
    bail_qs1 = tokenizer.from_list_format([
        {'image': full_img_path},
        {'text': f'<img>{full_img_path}</img>{bail_qs} Answer:'},])

    # print("task-hwr")
    # hwr = qwenvl(hwr_prompt1)
    # print("task-phwr")
    # phwr = qwenvl(p_hwr_prompt1)
    # print("task-pphwr")
    # pphwr = qwenvl(pp_hwr_prompt1)
    # print("task-l_hwr")
    # l_hwr = qwenvl(label_qs1)
    # print("task-l_phwr")
    # l_phwr = qwenvl(p_label_qs1)
    # print("task-l_pphwr")
    # l_pphwr = qwenvl(pp_label_qs1)
    # print("task-doc_vqa")
    # doc_vqa = qwenvl(docvqa_qs1)
    # print("task-bb")
    # bb_vqa = qwenvl(bb_qs1)


    if root_img not in unique_image_list:
      print("task-time")
      time_vqa = qwenvl(time_qs1)
      print("task-bail")
      bail_vqa = qwenvl(bail_qs1)
      content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
      LRVQA.append(content)
      unique_image_list.append(root_img)



    ## evaluation
    ground_truth = d["answers"]

    # try:
    #   hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    # except:
    #   hwr_cer_error, hwr_wer_error = 100,100

    # try:
    #   phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    # except:
    #   phwr_cer_error, phwr_wer_error = 100,100

    # try:
    #   pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    # except:
    #   pphwr_cer_error, pphwr_wer_error = 100,100

    # try:
    #   l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    # except:
    #   l_hwr_cer_error, l_hwr_wer_error = 100,100

    # try:
    #   l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    # except:
    #   l_phwr_cer_error, l_phwr_wer_error = 100,100

    # try:
    #   l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    # except:
    #   l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    # try:
    #   doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    # except:
    #   doc_vqa_cer_error, doc_vqawer_error = 100,100

    # d["hwr_cer"] = hwr_cer_error
    # d["hwr_wer"] = hwr_wer_error
    # d["hwr_model_output"] = hwr
    # d["hwr_prompt"] = hwr_prompt

    # d["phwr_cer"] = phwr_cer_error
    # d["phwr_wer"] = phwr_wer_error
    # d["phwr_model_output"] = phwr
    # d["phwr_prompt"] = hwr_prompt

    # d["pphwr_cer"] = pphwr_cer_error
    # d["pphwr_wer"] = pphwr_wer_error
    # d["pphwr_model_output"] = pphwr
    # d["pphwr_prompt"] = hwr_prompt

    # d["l_hwr_cer"] = l_hwr_cer_error
    # d["l_hwr_wer"] = l_hwr_wer_error
    # d["l_hwr_model_output"] = l_hwr
    # d["l_hwr_prompt"] = label_qs

    # d["l_phwr_cer"] = l_phwr_cer_error
    # d["l_phwr_wer"] = l_phwr_wer_error
    # d["l_phwr_model_output"] = l_phwr
    # d["l_phwr_hwr_prompt"] = label_qs

    # d["l_pphwr_cer"] = l_pphwr_cer_error
    # d["l_pphwr_wer"] = l_pphwr_wer_error
    # d["l_pphwr_model_output"] = l_pphwr
    # d["l_pphwr_hwr_prompt"] = label_qs

    # d["doc_vqa_cer"] = doc_vqa_cer_error
    # d["doc_vqa_wer"] = doc_vqa_wer_error
    # d["doc_vqa_model_output"] = doc_vqa
    # d["doc_vqa_hwr_prompt"] = label_qs



    # d["bbox_model_output"] = bb_vqa
    # d["bbox_hwr_prompt"] = bb_qs

    # d["model_name"] = model_name

    # evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
# with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
#     json.dump(evaluated_data, outfile)

print(LRVQA)
# LRVQA = json.dumps(LRVQA)
# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-100+reason"}.json'), 'w') as outfile:
    json.dump(LRVQA,outfile)

question what is written in the image?
task-time
 23/12/2014
task-bail
 bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 21:18
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 161 hours
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 72 hours
task-bail
 Bailable
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
question what is written in the image?
task-time
 12.51 Hrs


**Image Padding Experiment**

In [ ]:
def image_padding(image,pad_size = 10):
  right = pad_size
  left = pad_size
  top = pad_size
  bottom = pad_size

  width, height = image.size

  new_width = width + right + left
  new_height = height + top + bottom

  result = Image.new(image.mode, (new_width, new_height), (255, 255, 255))

  result.paste(image, (left, top))

  return result

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image"

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-pad10"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 10)
    pad_img.save(padded_path)

    query = tokenizer.from_list_format([
        {'image': padded_path},
        {'text': f'<img>{padded_path}</img>{qs} Answer:'},
    ])

    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)


 tequila 1944
 2018
 jism13
 02-08-2013
 48123254379
 6/3
 apc
 lostprophets
 unanswerable
 believe
 e-hallwolff
 12345678
 unanswerable
 formant
 ornagean
 kpd/feo203f
 a-tte-hed l-hote- lie-ky
 pi
 3p1plhc
 in re nuncata canonice
 to the office-in-charge, police station with regards, k. ramamohana rao
 www.alexa.com
 help
 art commissioner
 cfg
 barf
 aigis
 2018
 0718
 unanswerable
 2.391338
 373
 23.15 hrs
 sunday
 korean language
 21.15
 아시아
 23/11/05
 alpankar sardar
 babu sasolote
 thomas
 reproduce
 2e93381pc
 srilanka
 police
 mohammed ali gilani
 coors light
 unanswerable
 penrose
 micdoheoi
 bn
 a year
 q1me
 experience
 191118
 27/9/338
 911
 kairos
 bnl145
 a plus is my
 19118
 911
 app
 azizul haque taragola
 gur dukh bhai
 elhefe
 2/79/338 i.e. pe
 s.l. a.m. p.a.
 unanswerable
 isle of police
 point family mission statement
 arf
 q4bqbn
 barrett
 begurath
 2019
 hiragana
 12/12/19
 ipc
 2+4/938/499
 1962
 21375
 elizabet
 16130
 leilalila
 ghost
 1912
 jordi jordi
 af ha

Image padding 20

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image"

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-pad20"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 20)
    pad_img.save(padded_path)

    query = tokenizer.from_list_format([
        {'image': padded_path},
        {'text': f'<img>{padded_path}</img>{qs} Answer:'},
    ])

    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)


 shigematsu
 12:27
 isla
 02.02.2013
 pi
 50/6/3=7
 spc
 lost
 jian yi shi jiu
 memento mori
 e1234567890
 12345678
 jolly
 formant: ashma xhatoom
 gondolier
 kpd7f003f
 ahaehed horeahwird
 pi
 271 glpe
 in re penaranda banerjee
 help of the office-in-charge, police station with regards, norman cephas
 act test practice
 help
 ant commissioned
 cfr
 bnf
 alypia
 2018
 0718
 빅뱅
 2.29438
 373
 28.15 hrs
 sunday
 ojline
 21:15
 미나리
 23
 alipankar sardar
 babu sardate
 tachan
 reproduce below
 2e93381pc
 sr l maulik
 policy
 moham lad ghoul
 coors light
 jones
 amp
 unanswerable
 the impluse bsn
 dr. h. g. volkmar
 july 2018
 1918
 19118
 2991398
 gill
 at 18:54
 bjjj
 it is my
 191118
 911
 apprxx lthiu
 aziz
 gulab jamun
 attached herewith
 279/338
 s l a m y p a l
 unanswerable
 act of police
 font commission
 jell
 24 fevriy
 batesat
 boglioli
 2019
 513
 16-12-19
 ipc
 2pi/938/149
 1362
 2135
 ictheil9
 16.230 k
 16/2=8
 www.yourdomain.com
 1362
 egajul jarofdar
 4 habibur tarofder
 g

Prompt with label name

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-labelname"

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    # qs = d['question']

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)
    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])
    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name
    d["question"] = qs

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)


question what is the PoliceStation written in the image?
 51
question what is the Year written in the image?
 1998
question what is the FirNum written in the image?
 75173
question what is the Date written in the image?
 02-02-2013
question what is the Sections written in the image?
 147 148 127 131 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264
question what is the OtherActs written in the image?
 unanswerable
question what is the Sections written in the image?
 pce
question what is the GDEntNum written in the image?
 1024
question what is the 

Prompt with label name and image padding

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image"

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-labelname-pad10"
total_cer,total_wer = 0,0
avg_count = 0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 10)
    pad_img.save(padded_path)

    query = tokenizer.from_list_format([
        {'image': padded_path},
        {'text': f'<img>{padded_path}</img>{qs} Answer:'},
    ])

    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

question what is the PoliceStation written in the image?
 134
question what is the Year written in the image?
 2018
question what is the FirNum written in the image?
 75113
question what is the Date written in the image?
 02-08-2013
question what is the Sections written in the image?
 1481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481481
question what is the OtherActs written in the image?
 unanswerable
question what is the Sections written in the image?
 apa
question what is the GDEntNum written in the image?
 105716
question what is t

Label Name with Image Padding 20

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

out_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image"

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-labelname-pad20"
total_cer,total_wer = 0,0
avg_count = 0
for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'])
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    padded_path = os.path.join(out_folder,d['image_path'])

    pad_img = image_padding(image,pad_size = 20)
    pad_img.save(padded_path)

    query = tokenizer.from_list_format([
        {'image': padded_path},
        {'text': f'<img>{padded_path}</img>{qs} Answer:'},
    ])

    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)

print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

question what is the PoliceStation written in the image?
 134
question what is the Year written in the image?
 2018
question what is the FirNum written in the image?
 jislla
question what is the Date written in the image?
 02-02-2013
question what is the Sections written in the image?
 147 148 123 135 456 789
question what is the OtherActs written in the image?
 50/6/3
question what is the Sections written in the image?
 spc
question what is the GDEntNum written in the image?
 1971
question what is the GDTime written in the image?
 2012
question what is the ReceivedDate written in the image?
 27 Apr 2010 17:17:05
question what is the OOODate written in the image?
 12/12/09
question what is the ReceivedTime written in the image?
 12:25:17
question what is the GDNumber written in the image?
 35
question what is the CompName written in the image?
 formant
question what is the Nationality written in the image?
 french
question what is the CompAddress written in the image?
 70037
question w

In [ ]:
pred.shape

torch.Size([1, 540])

In [ ]:
print(model)

### Whole document image

In [ ]:
import json
import os
import json
import torch
import os
import json
from tqdm import tqdm
from PIL import Image
import math

data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"
# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)

# data = data[:10]
evaluated_data = []
model_name = "Qwen-VL-docvqa"
total_cer,total_wer = 0,0
avg_count = 0

for d in data:
    # print("Data",data[i])
    img_path = os.path.join(image_folder, d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg")
    print("image path",img_path)
    image = Image.open(img_path).convert("RGB")
    qs = d['question']

    label_name = d["label_name"]
    qs = "what is the " + label_name + " written in the image?"
    print("question", qs)

    query = tokenizer.from_list_format([
        {'image': img_path},
        {'text': f'<img>{img_path}</img>{qs} Answer:'},
    ])
    inputs = tokenizer(query, return_tensors='pt')
    inputs = inputs.to(model.device)
    pred = model.generate(**inputs)
    response = tokenizer.decode(pred.cpu()[0], skip_special_tokens=True)
    generated_text = response.split("Answer:")[1].split("<|endoftext|>")[0]
    # print(response)
    print(generated_text)

    # response, history = model.chat(tokenizer, query=query, history=None)
    # print(response)


    ## evaluation
    ground_truth = d["answers"]
    try:
      cer_error, wer_error = cer_wer(generated_text, ground_truth)
      total_cer += cer_error
      total_wer += wer_error
      avg_count +=1
    except:
      cer_error, wer_error = 100,100
    d["cer"] = cer_error
    d["wer"] = wer_error
    d["model_output"] = generated_text
    d["model_name"] = model_name

    evaluated_data.append(d)

if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json')):
  with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name}.json'), 'w') as outfile:
      json.dump(evaluated_data, outfile)
print(f'Overall CER {total_cer/avg_count}')
print(f'Overall WER {total_wer/avg_count}')

image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the PoliceStation written in the image?
 10240
image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Year written in the image?
 2015
image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the FirNum written in the image?
 15-2418
image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Date written in the image?
 19/12/2012
image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport PSAIRPORT-0019-2018-1020__1.jpg
question what is the Sections written in the image?
 188, 190
image path /content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images/Airport P

# **TrOCR -Evaluation**

In [ ]:
!pip install jiwer

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 58.2 MB/s eta 0:00:00


In [ ]:
from jiwer import cer
from jiwer import wer
def cer_wer(generated_text, ground_truth):
  cer_error = cer(ground_truth,generated_text)
  wer_error = wer(ground_truth,generated_text)
  return cer_error, wer_error

In [ ]:
#https://huggingface.co/docs/transformers/main/model_doc/trocr

from transformers import TrOCRProcessor
from transformers import VisionEncoderDecoderModel
import torch
import requests
from PIL import Image
from matplotlib.pyplot import imshow
%matplotlib inline

# img_url = '/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/images/Airport PSAIRPORT-0004-2017-2711__1_17.jpg'
# image = Image.open(img_url).convert('RGB')


processor = TrOCRProcessor.from_pretrained("microsoft/trocr-base-handwritten")
model = VisionEncoderDecoderModel.from_pretrained("microsoft/trocr-base-handwritten")



# imshow(image)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/224 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.12k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/772 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/4.17k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.33G [00:00<?, ?B/s]

Some weights of VisionEncoderDecoderModel were not initialized from the model checkpoint at microsoft/trocr-base-handwritten and are newly initialized: ['encoder.pooler.dense.bias', 'encoder.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


generation_config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
def trocr_model(image_path):
  image = Image.open(image_path).convert('RGB')
  # calling the processor is equivalent to calling the feature extractor
  pixel_values = processor(image, return_tensors="pt").pixel_values
  print(pixel_values.shape)

  generated_ids = model.generate(pixel_values)
  generated_text = processor.batch_decode(generated_ids, skip_special_tokens=True)[0]
  print("generated_text", generated_text)

  return generated_text

In [ ]:
import json
import os
device = "cuda" if torch.cuda.is_available() else "cpu"
data_path = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/ocr_dataset_small.json"
image_folder = "/content/drive/MyDrive/ocr_data/images"
pad10_image_folder =  "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image10"
pad20_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/padded_image20"
master_image_folder = "/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/images"


annotation_path = r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/master/master_dataset.json"

# model_vicuna.to(device)
with open(data_path, "r") as f:
    data = json.load(f)
# data = data[:3]


img_count = {}
labels = []
filt_data = []
for d in data:
  image_name = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
  if (len(filt_data) < 25):
    if not "signature" in d["label_name"].lower():
      if image_name not in list(img_count.keys()):

        img_count[image_name] = []

      if (len(img_count[image_name])<5):
        # else:
        img_count[image_name].append(image_name)
        labels.append(d["label_name"])
        filt_data.append(d)


evaluated_data = []
model_name = "TrOCR"

with open(annotation_path, 'r', encoding='utf8') as fin:
    orig_annotation = json.load(fin)

images = orig_annotation["images"]
annotations = orig_annotation["annotations"]
categories = orig_annotation["categories"]


unique_image_list = []
LRVQA = []
for d in filt_data:
    # print("Data",data[i])



    img_path = os.path.join(image_folder, d['image_path'])

    p_img_path = os.path.join(pad10_image_folder, d['image_path'])
    pp_img_path = os.path.join(pad20_image_folder, d['image_path'])

    root_img = d['image_path'].split("__")[0]+"__"+d['image_path'].split("__")[1].split("_")[0]+".jpg"
    full_img_path = os.path.join(master_image_folder, root_img )

    # hwr_image = Image.open(img_path).convert("RGB")
    # p_img = Image.open(p_img_path).convert("RGB")
    # pp_img = Image.open(pp_img_path).convert("RGB")
    # full_img = Image.open(full_img_path).convert("RGB")




    filtered_img = [img for img in images if img["file_name"] == root_img]
    filtered_img = filtered_img[0]

    filtered_id = filtered_img["id"]

    filtered_annotation = [ann for ann in annotations if ann["image_id"] == filtered_id]
    label_bbox = []
    for each_ann in filtered_annotation:
      cat_id = each_ann["category_id"]
      category_name = [cat["name"] for cat in categories if cat["id"] == cat_id]
      category_name = category_name[0]
      if category_name == d["label_name"]:
        label_bbox = each_ann["bbox"]


    #qs = d['question']
    # qs = qs+"\nAnswer the question using a single word or phrase."
    # prompt = "Question:" + qs + "? Answer:"

    qs = d['question']

    # query = tokenizer.from_list_format([
    #     {'image': img_path},
    #     {'text': f'<img>{img_path}</img>{qs} Answer:'},
    # ])

    # #qs = qs+" Answer the question using a single word or phrase."
    # # prompt = "Question:" + qs + "? Answer:"
    # # query = f'<img>{img_path}</img> {qs} Answer: ' #VQA


    hwr_prompt = f'{qs} Answer: ' #VQA
    # hwr_prompt1 = tokenizer.from_list_format([
    #     {'image': img_path},
    #     {'text': f'<img>{img_path}</img>{qs} Answer:'},])
    p_hwr_prompt = f'{qs} Answer: ' #VQA
    # p_hwr_prompt1 = tokenizer.from_list_format([
    #     {'image': p_img_path},
    #     {'text': f'<img>{p_img_path}</img>{qs} Answer:'},])
    pp_hwr_prompt = f'<img>{pp_img_path}</img> {qs} Answer: ' #VQA
    # pp_hwr_prompt1 = tokenizer.from_list_format([
    #     {'image': pp_img_path},
    #     {'text': f'<img>{pp_img_path}</img>{qs} Answer:'},])

    # label_name = d["label_name"]
    # label_qs = "what is the " + label_name + "written in the image?"
    # label_qs1 = tokenizer.from_list_format([
    #     {'image': img_path},
    #     {'text': f'<img>{img_path}</img>{label_qs} Answer:'},])
    # print("question", qs)
    # p_label_qs = "what is the " + label_name + " written in the image?"
    # p_label_qs1 = tokenizer.from_list_format([
    #     {'image': p_img_path},
    #     {'text': f'<img>{p_img_path}</img>{p_label_qs} Answer:'},])

    # pp_label_qs = "what is the " + label_name + " written in the image?"
    # pp_label_qs1 = tokenizer.from_list_format([
    #     {'image': pp_img_path},
    #     {'text': f'<img>{pp_img_path}</img>{pp_label_qs} Answer:'},])

    # docvqa_qs = "what is the " + label_name + " written in the image?"
    # docvqa_qs1 = tokenizer.from_list_format([
    #     {'image': full_img_path},
    #     {'text': f'<img>{full_img_path}</img>{docvqa_qs} Answer:'},])

    # bb_qs = "what is the bounding box for " + label_name + "in the image?"
    # bb_qs1 = tokenizer.from_list_format([
    #     {'image': full_img_path},
    #     {'text': f'<img>{full_img_path}</img>{bb_qs} Answer:'},])

    # time_qs = "What is the difference in time between the occurrence of the event and when it was reported?"
    # time_qs1 = tokenizer.from_list_format([
    #     {'image': full_img_path},
    #     {'text': f'<img>{full_img_path}</img>{time_qs} Answer:'},])
    # bail_qs = """Are the charges against accused bailable or not? If any of the charges are non-bailable answer "Non-bailable" else "Bailable"."""
    # bail_qs1 = tokenizer.from_list_format([
    #     {'image': full_img_path},
    #     {'text': f'<img>{full_img_path}</img>{bail_qs} Answer:'},])

    print("task-hwr")
    hwr = trocr_model(img_path)
    print("task-phwr")
    phwr = trocr_model(p_img_path)
    print("task-pphwr")
    pphwr = trocr_model(pp_img_path)
    print("task-l_hwr")
    # l_hwr = qwenvl(label_qs1)
    # print("task-l_phwr")
    # l_phwr = qwenvl(p_label_qs1)
    # print("task-l_pphwr")
    # l_pphwr = qwenvl(pp_label_qs1)
    # print("task-doc_vqa")
    # doc_vqa = qwenvl(docvqa_qs1)
    # print("task-bb")
    # bb_vqa = qwenvl(bb_qs1)


    # if root_img not in unique_image_list:
    #   print("task-time")
    #   time_vqa = qwenvl(time_qs1)
    #   print("task-bail")
    #   bail_vqa = qwenvl(bail_qs1)
    #   content = {"time_vqa":time_vqa,"bail_vqa":bail_vqa,"time_qs":time_qs,"bail_qs":bail_qs,"image_name":root_img,"time_gt":"","bail_gt":""}
    #   LRVQA.append(content)
    #   unique_image_list.append(root_img)



    ## evaluation
    ground_truth = d["answers"]

    try:
      hwr_cer_error, hwr_wer_error = cer_wer(hwr, ground_truth)
    except:
      hwr_cer_error, hwr_wer_error = 100,100

    try:
      phwr_cer_error, phwr_wer_error = cer_wer(phwr, ground_truth)
    except:
      phwr_cer_error, phwr_wer_error = 100,100

    try:
      pphwr_cer_error, pphwr_wer_error = cer_wer(pphwr, ground_truth)
    except:
      pphwr_cer_error, pphwr_wer_error = 100,100

    # try:
    #   l_hwr_cer_error, l_hwr_wer_error = cer_wer(l_hwr, ground_truth)
    # except:
    #   l_hwr_cer_error, l_hwr_wer_error = 100,100

    # try:
    #   l_phwr_cer_error, l_phwr_wer_error = cer_wer(l_phwr, ground_truth)
    # except:
    #   l_phwr_cer_error, l_phwr_wer_error = 100,100

    # try:
    #   l_pphwr_cer_error, l_pphwr_wer_error = cer_wer(l_pphwr, ground_truth)
    # except:
    #   l_pphwr_cer_error, l_pphwr_wer_error = 100,100

    # try:
    #   doc_vqa_cer_error, doc_vqa_wer_error = cer_wer(doc_vqa, ground_truth)
    # except:
    #   doc_vqa_cer_error, doc_vqawer_error = 100,100

    d["hwr_cer"] = hwr_cer_error
    d["hwr_wer"] = hwr_wer_error
    d["hwr_model_output"] = hwr
    d["hwr_prompt"] = hwr_prompt

    d["phwr_cer"] = phwr_cer_error
    d["phwr_wer"] = phwr_wer_error
    d["phwr_model_output"] = phwr
    d["phwr_prompt"] = hwr_prompt

    d["pphwr_cer"] = pphwr_cer_error
    d["pphwr_wer"] = pphwr_wer_error
    d["pphwr_model_output"] = pphwr
    d["pphwr_prompt"] = hwr_prompt

    # d["l_hwr_cer"] = l_hwr_cer_error
    # d["l_hwr_wer"] = l_hwr_wer_error
    # d["l_hwr_model_output"] = l_hwr
    # d["l_hwr_prompt"] = label_qs

    # d["l_phwr_cer"] = l_phwr_cer_error
    # d["l_phwr_wer"] = l_phwr_wer_error
    # d["l_phwr_model_output"] = l_phwr
    # d["l_phwr_hwr_prompt"] = label_qs

    # d["l_pphwr_cer"] = l_pphwr_cer_error
    # d["l_pphwr_wer"] = l_pphwr_wer_error
    # d["l_pphwr_model_output"] = l_pphwr
    # d["l_pphwr_hwr_prompt"] = label_qs

    # d["doc_vqa_cer"] = doc_vqa_cer_error
    # d["doc_vqa_wer"] = doc_vqa_wer_error
    # d["doc_vqa_model_output"] = doc_vqa
    # d["doc_vqa_hwr_prompt"] = label_qs



    # d["bbox_model_output"] = bb_vqa
    # d["bbox_hwr_prompt"] = bb_qs

    d["model_name"] = model_name

    evaluated_data.append(d)

# if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR"}.json')):
with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_HWR-25"}.json'), 'w') as outfile:
    json.dump(evaluated_data, outfile)




# print(LRVQA)
# # LRVQA = json.dumps(LRVQA)
# # if not os.path.exists(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA"}.json')):
# with open(os.path.join(r"/content/drive/MyDrive/My_PhD_Research/FIR_FORM/datasets/OCR/eval_output",f'{model_name+"_LRVQA-25-V2"}.json'), 'w') as outfile:
#     json.dump(LRVQA,outfile)

task-hwr
torch.Size([1, 3, 384, 384])


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1168: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


generated_text diffident
task-phwr
torch.Size([1, 3, 384, 384])
generated_text stit-post.
task-pphwr
torch.Size([1, 3, 384, 384])
generated_text airport.
task-l_hwr
task-hwr
torch.Size([1, 3, 384, 384])
generated_text rightering
task-phwr
torch.Size([1, 3, 384, 384])
generated_text raleigh.
task-pphwr
torch.Size([1, 3, 384, 384])
generated_text sidets.
task-l_hwr
task-hwr
torch.Size([1, 3, 384, 384])
generated_text jelfle.
task-phwr
torch.Size([1, 3, 384, 384])
generated_text istila.
task-pphwr
torch.Size([1, 3, 384, 384])
generated_text ishes.
task-l_hwr
task-hwr
torch.Size([1, 3, 384, 384])
generated_text appropriators
task-phwr
torch.Size([1, 3, 384, 384])
generated_text obedience
task-pphwr
torch.Size([1, 3, 384, 384])
generated_text obedience.
task-l_hwr
task-hwr
torch.Size([1, 3, 384, 384])
generated_text 1477448/ 3233154/3.91
task-phwr
torch.Size([1, 3, 384, 384])
generated_text 1977-ABP.3/35AF3/91
task-pphwr
torch.Size([1, 3, 384, 384])
generated_text willigate assistant
task-l